# 色空間の変換
## 目的
* このチュートリアルでは、画像の色空間を変換する方法を学ぶ．例えばカラー空間からグレースケール空間へ変換したり、BGR空間からHSV空間へ変換したりできるようになる．
* さらに，動画の中で特定の色を持つ物体を検出する方法も学ぶ．
* 次の関数の使い方を学ぶ : <A HREF="http://docs.opencv.org/3.0-beta/modules/imgproc/doc/miscellaneous_transformations.html?highlight=cv2.cvtcolor#cv2.cvtColor" target="_blank">cv2.cvtColor()</A>, <A HREF="http://docs.opencv.org/3.0-beta/modules/core/doc/operations_on_arrays.html?highlight=cv2.inrange#cv2.inRangec" target="_blank">v2.inRange()</A>.

## 色変換の変換
OpenCVは150種類以上の色空間の変換を用意しているが，その中で最も広く使われている変換方法は、$BGR \leftrightarrow Gray$変換と$BGR \leftrightarrow HSV$変換である。この２つを詳しく見ていく．

色変換に使う関数は <A HREF="http://docs.opencv.org/3.0-beta/modules/imgproc/doc/miscellaneous_transformations.html?highlight=cv2.cvtcolor#cv2.cvtColor" target="_blank">cv2.cvtColor(image, flag)</A> である．ここで `image`は画像データ、`flag` は色変換の種類を指定するフラグである．

$BGR \rightarrow Gray$変換には `cv2.COLOR_BGR2GRAY` フラグ，$BGR \rightarrow HSV$変換には `cv2.COLOR_BGR2HSV` フラグを指定する．その他のフラグは，次のコマンドを実行すれば表示される :

In [1]:
import cv2
flags = [i for i in dir(cv2) if i.startswith('COLOR_')]
print(flags)

['COLOR_BAYER_BG2BGR', 'COLOR_BAYER_BG2BGR_EA', 'COLOR_BAYER_BG2BGR_VNG', 'COLOR_BAYER_BG2GRAY', 'COLOR_BAYER_BG2RGB', 'COLOR_BAYER_BG2RGB_EA', 'COLOR_BAYER_BG2RGB_VNG', 'COLOR_BAYER_GB2BGR', 'COLOR_BAYER_GB2BGR_EA', 'COLOR_BAYER_GB2BGR_VNG', 'COLOR_BAYER_GB2GRAY', 'COLOR_BAYER_GB2RGB', 'COLOR_BAYER_GB2RGB_EA', 'COLOR_BAYER_GB2RGB_VNG', 'COLOR_BAYER_GR2BGR', 'COLOR_BAYER_GR2BGR_EA', 'COLOR_BAYER_GR2BGR_VNG', 'COLOR_BAYER_GR2GRAY', 'COLOR_BAYER_GR2RGB', 'COLOR_BAYER_GR2RGB_EA', 'COLOR_BAYER_GR2RGB_VNG', 'COLOR_BAYER_RG2BGR', 'COLOR_BAYER_RG2BGR_EA', 'COLOR_BAYER_RG2BGR_VNG', 'COLOR_BAYER_RG2GRAY', 'COLOR_BAYER_RG2RGB', 'COLOR_BAYER_RG2RGB_EA', 'COLOR_BAYER_RG2RGB_VNG', 'COLOR_BGR2BGR555', 'COLOR_BGR2BGR565', 'COLOR_BGR2BGRA', 'COLOR_BGR2GRAY', 'COLOR_BGR2HLS', 'COLOR_BGR2HLS_FULL', 'COLOR_BGR2HSV', 'COLOR_BGR2HSV_FULL', 'COLOR_BGR2LAB', 'COLOR_BGR2LUV', 'COLOR_BGR2Lab', 'COLOR_BGR2Luv', 'COLOR_BGR2RGB', 'COLOR_BGR2RGBA', 'COLOR_BGR2XYZ', 'COLOR_BGR2YCR_CB', 'COLOR_BGR2YCrCb', 'COLOR_BGR

<font color="blue">Note</font>:  HSVとは，Hueが色相，Saturation(Chroma)が彩度，Value(Lightness)が明度である．それぞれHueは`[0,179]`, Saturationは`[0,255]`，Valueは`[0,255]`の範囲の値をとるが、使用するソフトウェアによっては値の範囲が異なるので，OpenCVで得られた値と別ソフトウェアで得られた値を比較する場合は，値の正規化をしなければならない．

## 物体追跡
BGR画像をHSV画像へ変換する方法を学んだので，この方法を使って特定の色を持つ物体の検出ができるようになる．HSV空間では，RGB空間より色を表現するのが簡単だからである．ここでは青色をした物体の検出を試みよう．処理の流れは以下のようになる:
* 動画のフレーム(画像)を取得
* 画像をBGR空間からHSV空間へ色変換
* HSV空間上で，青色に対応する領域を閾値処理により見つける
* 青色の物体だけを検出できたので、それに対して好きな処理ができる
詳細なコメントをつけたコードを次に示す

In [ ]:
import cv2
import numpy as np

cap = cv2.VideoCapture(0)

while(True):

    # 一フレーム取り出す
    _, frame = cap.read()

    # BGR空間から HSV空間に変換
    hsv = cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)

    # HSV空間で青色の範囲を定義
    lower_blue = np.array([110,50,50])
    upper_blue = np.array([130,255,255])

    # HSV イメージから青い物体だけを取り出すための閾値
    mask = cv2.inRange(hsv, lower_blue, upper_blue)

    # ビットごとのAND演算で元画像をマスク
    res = cv2.bitwise_and(frame,frame, mask= mask)

    cv2.imshow('frame',frame)
    cv2.imshow('mask',mask)
    cv2.imshow('res',res)

    if cv2.waitKey(5) & 0xFF == 27:
        break

cv2.destroyAllWindows()

# Notebookの場合はこれが必要
for _ in range(5):
    cv2.waitKey(1)


結果を以下に示す:
<img src="http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/_images/frame.jpg"  width=150%/>

<font color="blue">Note</font>: 画像中にいくつかノイズが見えるが、このノイズの消し方は後のチュートリアルで紹介する．

<font color="blue">Note</font>: ここで紹介した方法は物体追跡の最も単純な方法である．輪郭処理に関する関数の使用方法を学べば，物体の重心位置を計算したり、カメラの前で手を振って図形を描くなど、いろいろな処理が行えるようになる．

## 追跡すべき色(HSV)を調べる方法
<A HREF="http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/py_tutorials/py_imgproc/py_colorspaces/www.stackoverflow.com" target="_blank">stackoverflow.com</A>(技術者の質問サイト)でよく見る質問の一つがこれである．これはとても簡単で、まさに画像の色変換を行う `cv2.cvtColor()` 関数で実現できる。画像データを引数とする代わりに、特定の色の値(BGR値)を引数とすればよいのである。例えば，緑色に対応するHSVでの色を知りたければ，Pythonのターミナル上で次のようにコマンドを実行すればよい

In [2]:
import cv2
import numpy as np
green = np.uint8([[[0,255,0 ]]])
hsv_green = cv2.cvtColor(green,cv2.COLOR_BGR2HSV)
print( hsv_green )

[[[ 60 255 255]]]


これにより、下界と上界の値をそれぞれ `[H-10, 100,100]`と`[H+10, 255, 255]` に設定すればいいことが分かる．なおこれ以外の方法，例えばGIMPのような画像編集ソフトを使っても色相の値を調べることができる．ただし，(前に注意したように！)OpenCVが設定している色相の範囲に正規化する必要があることをお忘れなく．

<font color="blue">Note</font>: このような答え方だとやはりstackoverflow.com(IT技術者のための質問応答サイト)に頼る人が出てくるだろう。HSVでは色はHueの値でほぼ決まるので、緑の場合Hue値の下限は60-10=50, 上限は60+10=70くらいとする。S値とV値は大きい方が鮮やかで明るくなり、小さいと黒くなるので、普通の色を考えているのであれば大きい値のほうがよい。その意味で`[50,100,100]`が下限、`[70,255,255]`が上限と答えているのである。なお、<A HREF="http://www.petitmonte.com/javascript/rgb_hsv_convert.html" target="_blank">このサイト</A>(ただしHSVの値の範囲がOpenCVとは異なることに注意)などでも色を確かめることができる。


## 課題
1. 色を一つに限定せず、例えば赤，青，緑それぞれの色の物体を同時に検出する方法を考えて実装してみよ．

## 目次
* [最初に戻る]( http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/usingOpenCV.html )
* 一つ上: OpenCVを使った画像処理<BR>
     OpenCVが提供する様々な画像処理の関数について学ぶ
* 前の学習項目 [コードの性能評価と改善方法  optimization.ipynb ](http://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/optimization.html)<BR>
処理をして結果を得ることは重要だが，最速の方法で結果を得ることはもっと重要．ここでは実装したコードの処理速度の確認方法やコードの最適化等について学ぶ．
* 次の学習項目 [画像の幾何変換 geometricTransformations.ipynb](ttp://lang.sist.chukyo-u.ac.jp/Classes/OpenCV/Notebook/geometricTransformations.html)<BR>
回転や並進といった幾何変換を画像に適用する方法を学ぶ．
